In [7]:
import pandas as pd
import glob 

In [24]:
filepath = r'C:\Users\User\Downloads\포트홀 주행 데이터\2023-05-30_05-10-55'
for filename in glob.glob(filepath+'\*.csv'):
    try :
        df= pd.read_csv(filename)
        print(filename.replace(filepath,''),df.shape,df.columns)    
    except:
        continue
    #

\Accelerometer.csv (15201, 5) Index(['time', 'seconds_elapsed', 'z', 'y', 'x'], dtype='object')
\AccelerometerUncalibrated.csv (15201, 5) Index(['time', 'seconds_elapsed', 'z', 'y', 'x'], dtype='object')
\Barometer.csv (145, 4) Index(['time', 'seconds_elapsed', 'relativeAltitude', 'pressure'], dtype='object')
\Gravity.csv (15201, 5) Index(['time', 'seconds_elapsed', 'z', 'y', 'x'], dtype='object')
\Gyroscope.csv (15201, 5) Index(['time', 'seconds_elapsed', 'z', 'y', 'x'], dtype='object')
\GyroscopeUncalibrated.csv (15201, 5) Index(['time', 'seconds_elapsed', 'z', 'y', 'x'], dtype='object')
\Location.csv (153, 12) Index(['time', 'seconds_elapsed', 'altitude', 'speedAccuracy',
       'bearingAccuracy', 'latitude', 'altitudeAboveMeanSeaLevel', 'bearing',
       'horizontalAccuracy', 'verticalAccuracy', 'longitude', 'speed'],
      dtype='object')
\Magnetometer.csv (15201, 5) Index(['time', 'seconds_elapsed', 'z', 'y', 'x'], dtype='object')
\MagnetometerUncalibrated.csv (15201, 5) Index(['

In [ ]:
print(df.shape,df.columns)

In [49]:
import psycopg2
import time
from datetime import timedelta,datetime

class DB():
    def __init__(self):
        self.conn=psycopg2.connect(
            host='localhost',
            dbname='postgres',
            user='postgres',
            password='ts4430!@',
            port='5432'
            ) # db에 접속
        self.conn.autocommit=True
        
    def db_add_report(self,report_id,report_x,report_y) :
        cur = self.conn.cursor() # 커서를 생성한다
        now=time.localtime()
        d=time.strftime('%Y-%m-%d %X', now)
        cur.execute(f'''
        insert into "TRAFFICAGENCY".report (report_id,report_x,report_y,timestamp)
        values ('{report_id}','{report_x}','{report_y}','{d}')
        ''')
        
    def db_get_near_point(self,dest_x,dest_y):
        cur = self.conn.cursor() # 커서를 생성한다
        now=datetime.now() 
        d_plus=now +timedelta(hours=1)
        d_plus=str("'"+d_plus.strftime('%Y-%m-%d %X')+"'")
        d_minus=now -timedelta(hours=1)
        d_minus=str("'"+d_minus.strftime('%Y-%m-%d %X')+"'")
        cur.execute(f'''
        select report_x, report_y
        from "TRAFFICAGENCY".report 
        where {dest_y} > report_y  - 0.000498 and {dest_y} <= report_y  + 0.000498
        and {dest_x} > report_x  - 0.000498 and {dest_x} <= report_x + 0.000498
        and timestamp between {d_minus} and {d_plus};


        ''')
        result=cur.fetchall()
        return result
    
    def db_add_pothole(pothole_id,pothole_location_x,pothole_location_y) :
        cur = self.conn.cursor() # 커서를 생성한다
        now=time.localtime()
        d=time.strftime('%Y-%m-%d %X', now)
        cur.execute(f'''
        insert into "TRAFFICAGENCY".pothole (pothole_id,pothole_location_x,pothole_location_y,timestamp)
        values ('{pothole_id}','{pothole_location_x}','{pothole_location_y}','{d}')
        ''')    
    


db = DB()
pothole_x = 123.123
pothole_y = 32.123
db.db_add_report(2,pothole_x,pothole_y)
result=db.db_get_near_point(pothole_x,pothole_y)

In [12]:
if len(result) >3 :
    value = 0
    for i in range(len(result)):
        value += result[i][0]
    average_x= (value / len(result))
    value2 = 0
    for i in range(len(result)):
        value2 += result[i][1]
    average_y= (value2 / len(result))
    db.db_add_pothole(1,average_x,average_y)


123.123
32.123


In [41]:
from datetime import timedelta,datetime
now=datetime.now() 
d_plus=now +timedelta(hours=1)
d_plus=str(d_plus.strftime('%Y-%m-%d %X'))
d_minus=now -timedelta(hours=1)
d_minus=str(d_minus.strftime('%Y-%m-%d %X'))


In [46]:
d_plus

'2023-07-17 17:43:29'

In [23]:
time.localtime() 

time.struct_time(tm_year=2023, tm_mon=7, tm_mday=17, tm_hour=16, tm_min=30, tm_sec=2, tm_wday=0, tm_yday=198, tm_isdst=0)

In [ ]:
select report_x, report_y 
from "TRAFFICAGENCY".report 
where 32.123 > report_y  - 0.000498 and 32.123 <= report_y  + 0.000498
and 123.123 > report_x  - 0.000498 and 123.123 <= report_x + 0.000498
and timestamp between {d_plus} and {d_minus}

pothole_x = 123.123
pothole_y = 32.123